
<div style="text-align: center; line-height: 0; padding-top: 9px;">
  <img src="https://databricks.com/wp-content/uploads/2018/03/db-academy-rgb-1200px.png" alt="Databricks Learning">
</div>



# Hyperparameter Tuning with Hyperopt

In this hands-on demo, you will learn how to leverage **Hyperopt**, a powerful optimization library, for efficient model tuning. We'll guide you through the process of performing **Bayesian hyperparameter optimization, demonstrating how to define the search space, objective function, and algorithm selection**. Throughout the demo, you will utilize *MLflow* to seamlessly track the model tuning process, capturing essential information such as hyperparameters, metrics, and intermediate results. By the end of the session, you will not only grasp the principles of hyperparameter optimization but also be proficient in finding the best-tuned model using various methods such as the **MLflow API** and **MLflow UI**.

**Learning Objectives:**

*By the end of this demo, you will be able to;*

* Utilize hyperopt for model tuning.

* Perform a Bayesian hyperparameter optimization using Hyperopt.

* Track model tuning process with MLflow.

* Query previous runs from an experiment using the `MLFlowClient`.

* Review an MLflow Experiment for the best run.

* Search and retrieve the best model.  


## Requirements

Please review the following requirements before starting the lesson:

* To run this notebook, you need to use one of the following Databricks runtime(s): **13.3.x-cpu-ml-scala2.12 13.3.x-scala2.12**


## Classroom Setup

Before starting the demo, run the provided classroom setup script. This script will define configuration variables necessary for the demo. Execute the following cell:

In [0]:
%run ../Includes/Classroom-Setup-02

Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.
Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.


Resetting the learning environment:
| dropping the catalog "labuser8100238_1734722509_1v9p_da"...(1 seconds)

Skipping install of existing datasets to "dbfs:/mnt/dbacademy-datasets/machine-learning-model-development/v01"

Validating the locally installed datasets:
| listing local files...(0 seconds)
| validation completed...(0 seconds total)
Creating & using the catalog "labuser8100238_1734722509_1v9p_da"...(2 seconds)


2024/12/20 19:40:19 INFO databricks.feature_store._compute_client._compute_client: Setting columns ['unique_id'] of table 'labuser8100238_1734722509_1v9p_da.default.diabetes' to NOT NULL.
2024/12/20 19:40:26 INFO databricks.feature_store._compute_client._compute_client: Setting Primary Keys constraint ['unique_id'] on table 'labuser8100238_1734722509_1v9p_da.default.diabetes'.
2024/12/20 19:40:44 INFO databricks.feature_store._compute_client._compute_client: Created feature table 'labuser8100238_1734722509_1v9p_da.default.diabetes'.



Predefined tables in "labuser8100238_1734722509_1v9p_da.default":
| diabetes

Predefined paths variables:
| DA.paths.working_dir: dbfs:/mnt/dbacademy-users/labuser8100238_1734722509@vocareum.com/machine-learning-model-development
| DA.paths.datasets:    dbfs:/mnt/dbacademy-datasets/machine-learning-model-development/v01

Setup completed (59 seconds)


**Other Conventions:**

Throughout this demo, we'll refer to the object `DA`. This object, provided by Databricks Academy, contains variables such as your username, catalog name, schema name, working directory, and dataset locations. Run the code block below to view these details:

In [0]:
print(f"Username:          {DA.username}")
print(f"Catalog Name:      {DA.catalog_name}")
print(f"Schema Name:       {DA.schema_name}")
print(f"Working Directory: {DA.paths.working_dir}")
print(f"Dataset Location:  {DA.paths.datasets}")

Username:          labuser8100238_1734722509@vocareum.com
Catalog Name:      labuser8100238_1734722509_1v9p_da
Schema Name:       default
Working Directory: dbfs:/mnt/dbacademy-users/labuser8100238_1734722509@vocareum.com/machine-learning-model-development
Dataset Location:  dbfs:/mnt/dbacademy-datasets/machine-learning-model-development/v01


## Prepare Dataset

Before we start fitting a model, we need to prepare dataset. First, we will load dataset, then we will split it to train and test sets.

### Load Dataset

In this demo we will be using the CDC Diabetes dataset. This dataset has been loaded and loaded to a feature table. We will use this feature table to load data.

In [0]:
import mlflow.data

# load data from the feature table
table_name = f"{DA.catalog_name}.{DA.schema_name}.diabetes"
diabetes_dataset = mlflow.data.load_delta(table_name=table_name)
diabetes_pd =diabetes_dataset.df.drop("unique_id").toPandas()

# review dataset and schema
display(diabetes_pd)
print(diabetes_pd.info())

Diabetes_binary HighBP HighChol CholCheck BMI Smoker Stroke HeartDiseaseorAttack PhysActivity Fruits Veggies HvyAlcoholConsump AnyHealthcare NoDocbcCost GenHlth MentHlth PhysHlth DiffWalk Sex Age Education Income 0.0 1.0 0.0 1.0 26.0 0.0 0.0 0.0 1.0 0.0 1.0 0.0 1.0 0.0 3.0 5.0 30.0 0.0 1.0 4.0 6.0 8.0 0.0 1.0 1.0 1.0 26.0 1.0 1.0 0.0 0.0 1.0 0.0 0.0 1.0 0.0 3.0 0.0 0.0 0.0 1.0 12.0 6.0 8.0 0.0 0.0 0.0 1.0 26.0 0.0 0.0 0.0 1.0 1.0 1.0 0.0 1.0 0.0 1.0 0.0 10.0 0.0 1.0 13.0 6.0 8.0 0.0 1.0 1.0 1.0 28.0 1.0 0.0 0.0 1.0 1.0 1.0 0.0 1.0 0.0 3.0 0.0 3.0 0.0 1.0 11.0 6.0 8.0 0.0 0.0 0.0 1.0 29.0 1.0 0.0 0.0 1.0 1.0 1.0 0.0 1.0 0.0 2.0 0.0 0.0 0.0 0.0 8.0 5.0 8.0 0.0 0.0 0.0 1.0 18.0 0.0 0.0 0.0 1.0 1.0 1.0 0.0 0.0 0.0 2.0 7.0 0.0 0.0 0.0 1.0 4.0 7.0 0.0 0.0 1.0 1.0 26.0 1.0 0.0 0.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 0.0 0.0 0.0 1.0 13.0 5.0 6.0 0.0 0.0 0.0 1.0 31.0 1.0 0.0 0.0 0.0 1.0 1.0 0.0 1.0 0.0 4.0 0.0 0.0 0.0 1.0 6.0 4.0 3.0 0.0 0.0 0.0 1.0 32.0 0.0 0.0 0.0 1.0 1.0 1.0 0.0 1.0 0.0 3.0 0.0 0.0 0.0 0.0 3.0 6.0 8.0 0.0 0.0 0.0 1.0 27.0 1.0 0.0 0.0 0.0 1.0 1.0 0.0 1.0 0.0 3.0 0.0 6.0 0.0 1.0 6.0 4.0 4.0 0.0 1.0 1.0 1.0 24.0 1.0 0.0 1.0 1.0 1.0 1.0 0.0 1.0 0.0 3.0 0.0 4.0 0.0 0.0 12.0 4.0 6.0 0.0 0.0 0.0 1.0 21.0 0.0 0.0 0.0 1.0 1.0 1.0 0.0 1.0 0.0 1.0 0.0 0.0 0.0 1.0 4.0 6.0 8.0 0.0 1.0 1.0 1.0 27.0 0.0 0.0 0.0 1.0 1.0 1.0 0.0 1.0 0.0 2.0 0.0 0.0 0.0 1.0 7.0 6.0 8.0 0.0 1.0 0.0 1.0 58.0 0.0 0.0 0.0 0.0 1.0 1.0 0.0 1.0 0.0 3.0 3.0 3.0 0.0 1.0 10.0 4.0 6.0 0.0 0.0 1.0 1.0 29.0 1.0 0.0 0.0 1.0 1.0 0.0 0.0 1.0 0.0 1.0 0.0 0.0 1.0 0.0 10.0 5.0 1.0 0.0 0.0 0.0 1.0 18.0 1.0 0.0 0.0 1.0 1.0 0.0 0.0 1.0 0.0 3.0 0.0 0.0 0.0 0.0 10.0 4.0 6.0 0.0 0.0 0.0 1.0 30.0 0.0 0.0 0.0 1.0 0.0 1.0 0.0 1.0 0.0 2.0 0.0 0.0 0.0 0.0 9.0 5.0 7.0 0.0 0.0 0.0 1.0 30.0 1.0 0.0 0.0 1.0 1.0 1.0 0.0 1.0 0.0 1.0 0.0 0.0 0.0 1.0 10.0 6.0 7.0 0.0 0.0 0.0 1.0 20.0 0.0 0.0 0.0 1.0 1.0 1.0 0.0 1.0 0.0 2.0 0.0 0.0 0.0 0.0 8.0 6.0 8.0 0.0 1.0 0.0 1.0 26.0 0.0 0.0 0.0 0.0 1.0 1.0 0.0 0.0 1.0 3.0 0.0 15.0 0.0 1.0 7.0 5.0 5.0 0.0 0.0 0.0 1.0 22.0 0.0 0.0 0.0 1.0 1.0 1.0 0.0 1.0 0.0 1.0 0.0 0.0 0.0 0.0 6.0 6.0 8.0 0.0 1.0 0.0 1.0 29.0 1.0 0.0 0.0 1.0 1.0 1.0 0.0 1.0 0.0 5.0 0.0 30.0 0.0 1.0 10.0 5.0 8.0 0.0 0.0 0.0 1.0 22.0 0.0 0.0 0.0 1.0 0.0 1.0 1.0 1.0 0.0 2.0 0.0 0.0 0.0 0.0 8.0 6.0 8.0 0.0 0.0 0.0 1.0 30.0 0.0 0.0 0.0 1.0 1.0 1.0 0.0 1.0 0.0 1.0 0.0 0.0 0.0 0.0 9.0 4.0 6.0 0.0 0.0 1.0 1.0 27.0 0.0 0.0 0.0 1.0 1.0 1.0 0.0 1.0 0.0 3.0 4.0 30.0 0.0 0.0 10.0 4.0 3.0 0.0 0.0 1.0 1.0 28.0 0.0 0.0 0.0 1.0 0.0 1.0 0.0 1.0 0.0 2.0 2.0 1.0 0.0 1.0 8.0 5.0 8.0 0.0 1.0 0.0 1.0 20.0 1.0 0.0 0.0 0.0 0.0 1.0 0.0 1.0 0.0 2.0 0.0 3.0 0.0 0.0 12.0 6.0 7.0 0.0 1.0 1.0 1.0 32.0 0.0 0.0 0.0 0.0 0.0 1.0 0.0 1.0 0.0 4.0 0.0 4.0 0.0 0.0 9.0 4.0 6.0 0.0 0.0 0.0 1.0 38.0 0.0 0.0 0.0 1.0 1.0 1.0 0.0 1.0 0.0 2.0 2.0 2.0 0.0 0.0 6.0 5.0 7.0 0.0 0.0 1.0 1.0 40.0 1.0 0.0 0.0 1.0 1.0 1.0 0.0 1.0 0.0 2.0 0.0 0.0 0.0 0.0 7.0 5.0 8.0 0.0 1.0 1.0 1.0 24.0 1.0 0.0 0.0 1.0 1.0 1.0 0.0 1.0 0.0 4.0 30.0 14.0 1.0 0.0 4.0 5.0 1.0 0.0 0.0 0.0 1.0 24.0 1.0 0.0 0.0 1.0 1.0 1.0 0.0 1.0 0.0 2.0 5.0 0.0 0.0 0.0 3.0 5.0 3.0 0.0 0.0 0.0 1.0 20.0 0.0 0.0 0.0 1.0 1.0 1.0 0.0 1.0 0.0 3.0 0.0 2.0 0.0 1.0 4.0 4.0 7.0 0.0 0.0 0.0 1.0 20.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 1.0 0.0 4.0 0.0 4.0 0.0 0.0 4.0 5.0 2.0 0.0 1.0 1.0 1.0 29.0 1.0 0.0 1.0 1.0 1.0 1.0 0.0 1.0 0.0 2.0 0.0 0.0 0.0 1.0 11.0 5.0 6.0 0.0 0.0 1.0 1.0 24.0 0.0 0.0 0.0 1.0 0.0 0.0 0.0 1.0 0.0 1.0 20.0 0.0 0.0 0.0 9.0 4.0 6.0 0.0 0.0 0.0 1.0 25.0 0.0 0.0 0.0 0.0 0.0 1.0 0.0 1.0 0.0 2.0 0.0 0.0 0.0 1.0 5.0 6.0 8.0 0.0 0.0 0.0 1.0 36.0 1.0 0.0 0.0 1.0 1.0 1.0 0.0 1.0 0.0 2.0 0.0 0.0 0.0 1.0 7.0 6.0 6.0 0.0 0.0 1.0 1.0 31.0 1.0 0.0 0.0 1.0 0.0 0.0 0.0 1.0 0.0 2.0 0.0 0.0 0.0 1.0 6.0 5.0 8.0 0.0 0.0 1.0 1.0 27.0 1.0 0.0 0.0 1.0 0.0 1.0 0.0 1.0 0.0 1.0 0.0 0.0 0.0 1.0 11.0 5.0 8.0 0.0 0.0 0.0 1.0 26.0 0.0 0.0 0.0 1.0 1.0 1.0 1.0 1.0 0.0 3.0 1.0 0.0 0.0 0.0 8.0 5.0 8.0 0.0 0.0 1.0 1.0 27.0 0.0 0.0 0.0 1.0 0.0 1.0 0.0 1.0 0.0 2.0 0.0 0.0 0.0 1.0 8.0 6.0 8.0 0.0 1.0 1.0 1.0 47.0 1.0 0.

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 70692 entries, 0 to 70691
Data columns (total 22 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   Diabetes_binary       70692 non-null  float64
 1   HighBP                70692 non-null  float64
 2   HighChol              70692 non-null  float64
 3   CholCheck             70692 non-null  float64
 4   BMI                   70692 non-null  float64
 5   Smoker                70692 non-null  float64
 6   Stroke                70692 non-null  float64
 7   HeartDiseaseorAttack  70692 non-null  float64
 8   PhysActivity          70692 non-null  float64
 9   Fruits                70692 non-null  float64
 10  Veggies               70692 non-null  float64
 11  HvyAlcoholConsump     70692 non-null  float64
 12  AnyHealthcare         70692 non-null  float64
 13  NoDocbcCost           70692 non-null  float64
 14  GenHlth               70692 non-null  float64
 15  MentHlth           


### Train/Test Split

Next, we will divide the dataset to training and testing sets.

In [0]:
from sklearn.model_selection import train_test_split

print(f"We have {diabetes_pd.shape[0]} records in our source dataset")

# split target variable into it's own dataset
target_col = "Diabetes_binary"
X_all = diabetes_pd.drop(labels=target_col, axis=1)
y_all = diabetes_pd[target_col]

# test / train split
X_train, X_test, y_train, y_test = train_test_split(X_all, y_all, train_size=0.95, random_state=42)
print(f"We have {X_train.shape[0]} records in our training dataset")
print(f"We have {X_test.shape[0]} records in our test dataset")

We have 70692 records in our source dataset
We have 67157 records in our training dataset
We have 3535 records in our test dataset


## Hyperparameter Tuning

### Define the Hyperparameter Search Space

Hyperopt uses a [Bayesian optimization algorithm](https://hyperopt.github.io/hyperopt/#algorithms) to perform a more intelligent search of the hyperparameter space. Therefore, **the initial space definition is effectively a prior distribution over the hyperparameters**, which will be used as the starting point for the Bayesian optimization process. 

Instead of defining a range or grid for each hyperparameter, we use [Hyperopt's parameter expressions](https://hyperopt.github.io/hyperopt/getting-started/search_spaces/#parameter-expressions) to define such prior distributions over parameter values.


In [0]:
from hyperopt import hp

dtc_param_space = {
  'criterion': hp.choice('dtree_criterion', ['gini', 'entropy']),
  'max_depth': hp.choice('dtree_max_depth',
                          [None, hp.uniformint('dtree_max_depth_int', 5, 50)]),
  'min_samples_split': hp.uniformint('dtree_min_samples_split', 2, 40),
  'min_samples_leaf': hp.uniformint('dtree_min_samples_leaf', 1, 20)
}

### Define the Optimization Function

We wrap our training code up as a function that we pass to hyperopt to optimize. The function takes a set of hyperparameter values as a `dict` and returns the validation loss score.

**💡 Note:** We are using `f1` score as the cross-validated loss metric. As we goal of optimization function is to minimize the loss, we are returning `-f1`, in other words, **we want to maximize the `f1` score**.

In [0]:
from math import sqrt

import mlflow
import mlflow.data
import mlflow.sklearn

from sklearn.tree import DecisionTreeClassifier
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
from sklearn.model_selection import cross_validate

from hyperopt import STATUS_OK

def tuning_objective(params):
  # start an MLFlow run
  with mlflow.start_run(nested=True) as mlflow_run:
    # Enable automatic logging of input samples, metrics, parameters, and models
    mlflow.sklearn.autolog(
        disable=False,
        log_input_examples=True,
        silent=True,
        exclusive=False)

    # set up our model estimator
    dtc = DecisionTreeClassifier(**params)
    
    # cross-validated on the training set
    validation_scores = ['accuracy', 'precision', 'recall', 'f1']
    cv_results = cross_validate(dtc, 
                                X_train, 
                                y_train, 
                                cv=5,
                                scoring=validation_scores)
    # log the average cross-validated results
    cv_score_results = {}
    for val_score in validation_scores:
      cv_score_results[val_score] = cv_results[f'test_{val_score}'].mean()
      mlflow.log_metric(f"cv_{val_score}", cv_score_results[val_score])

    # fit the model on all training data
    dtc_mdl = dtc.fit(X_train, y_train)

    # evaluate the model on the test set
    y_pred = dtc_mdl.predict(X_test)
    accuracy_score(y_test, y_pred)
    precision_score(y_test, y_pred)
    recall_score(y_test, y_pred)
    f1_score(y_test, y_pred)

    # return the negative of our cross-validated F1 score as the loss
    return {
      "loss": -cv_score_results['f1'],
      "status": STATUS_OK,
      "run": mlflow_run
    }

### Run in Hyperopt

After defining the *objective function*, we are ready to run this function with hyperopt. 

As you may have noticed, tuning process will need to test many models. We are going to create an instance of **`SparkTrials()` to parallelize hyperparameter tuning trials using Spark**. This is useful for distributing the optimization process across a Spark cluster.

`SparkTrials` takes a **`parallelism` parameter, which specifies how many trials are run in parallel**. This parameter will depend on the compute resources available for the cluster. You can read more about how to choose the optimal `parallelism` value in this [blog post](https://www.databricks.com/blog/2021/04/15/how-not-to-tune-your-model-with-hyperopt.html). 

For search algorithm, we will choose the **TPE (Tree-structured Parzen Estimator) algorithm for optimization (`algo=tpe.suggest`)**.

In [0]:
from hyperopt import SparkTrials, fmin, tpe

# set the path for mlflow experiment
mlflow.set_experiment(f"/Users/{DA.username}/Demo-2.1-Hyperparameter-Tuning-with-Hyperopt")

trials = SparkTrials(parallelism=4)
with mlflow.start_run(run_name="Model Tuning with Hyperopt Demo") as parent_run:
  fmin(tuning_objective,
      space=dtc_param_space,
      algo=tpe.suggest,
      max_evals=5,  # Increase this when widening the hyperparameter search space.
      trials=trials)

best_result = trials.best_trial["result"]
best_run = best_result["run"]

2024/12/20 19:40:57 INFO mlflow.tracking.fluent: Experiment with name '/Users/labuser8100238_1734722509@vocareum.com/Demo-2.1-Hyperparameter-Tuning-with-Hyperopt' does not exist. Creating a new experiment.
INFO:hyperopt-spark:Hyperopt with SparkTrials will automatically track trials in MLflow. To view the MLflow experiment associated with the notebook, click the 'Runs' icon in the notebook context bar on the upper right. There, you can view all runs.
INFO:hyperopt-spark:To view logs from trials, please check the Spark executor logs. To view executor logs, expand 'Spark Jobs' above until you see the (i) icon next to the stage from the trial job. Click it and find the list of tasks. Click the 'stderr' link for a task to view trial logs.


100%|██████████| 5/5 [00:34<00:00,  6.85s/trial, best loss: -0.7477902930835063]


INFO:hyperopt-spark:Total Trials: 5: 5 succeeded, 0 failed, 0 cancelled.


Note that we used a **nested run** while tracking the tuning process. This means we can access to the *parent_run* and child runs. One of the runs we would definitely be interested in is the *best_run*. Let's check out these runs.

In [0]:
parent_run.info.run_id

'087a91c6aa8347c8bac5342816163ea1'

In [0]:
best_run.info

<RunInfo: artifact_uri='dbfs:/databricks/mlflow-tracking/368426492796581/84a3c7a78eae445e9e385e54e45235fd/artifacts', end_time=None, experiment_id='368426492796581', lifecycle_stage='active', run_id='84a3c7a78eae445e9e385e54e45235fd', run_name='crawling-elk-932', run_uuid='84a3c7a78eae445e9e385e54e45235fd', start_time=1734723659425, status='RUNNING', user_id=''>

## Find the Best Run

In this section, we will search for registered models. There are couple ways for achieving this. We will show how to search runs using MLflow API, PySpark API and the UI.

### Find the Best Run - MLFlow API

Using the MLFlow API, you can search runs in an experiment, which returns results into a Pandas DafaFrame.

In [0]:
from mlflow.entities import ViewType

# search over all runs
hpo_runs_pd = mlflow.search_runs(
  experiment_ids=[parent_run.info.experiment_id],
  filter_string=f"tags.mlflow.parentRunId = '{parent_run.info.run_id}' AND attributes.status = 'FINISHED'",
  run_view_type=ViewType.ACTIVE_ONLY,
  order_by=["metrics.cv_f1 DESC"]
)

display(hpo_runs_pd)

run_id experiment_id status artifact_uri start_time end_time metrics.cv_precision metrics.training_recall_score metrics.training_precision_score metrics.cv_accuracy metrics.loss metrics.training_f1_score metrics.training_score metrics.training_roc_auc metrics.cv_recall metrics.training_accuracy_score metrics.cv_f1 metrics.training_log_loss params.dtree_min_samples_leaf params.splitter params.random_state params.criterion params.min_samples_split params.dtree_max_depth_int params.class_weight params.dtree_min_samples_split params.dtree_criterion params.dtree_max_depth params.min_weight_fraction_leaf params.max_leaf_nodes params.ccp_alpha params.min_samples_leaf params.max_depth params.min_impurity_decrease params.max_features tags.mlflow.runColor tags.mlflow.user tags.trial_status tags.mlflow.runName tags.estimator_class tags.mlflow.parentRunId tags.mlflow.log-model.history tags.fmin_uuid tags.mlflow.rootRunId tags.runSource tags.estimator_name 84a3c7a78eae445e9e385e54e45235fd 368426492796581 FINISHED dbfs:/databricks/mlflow-tracking/368426492796581/84a3c7a78eae445e9e385e54e45235fd/artifacts 2024-12-20T19:40:59.425Z 2024-12-20T19:41:19.116Z 0.7166073025685853 0.7618863260717423 0.7638499686468617 0.736364076484007 -0.7477902930835063 0.7614462413451514 0.7618863260717423 0.8422767781862777 0.7819779565087875 0.7618863260717423 0.7477902930835063 0.484407069875055 12.0 best None gini 33 10.0 None 33.0 0 1 0.0 None 0.0 12 10 0.0 None #da4c4c labuser8100238_1734722509@vocareum.com success crawling-elk-932 sklearn.tree._classes.DecisionTreeClassifier 087a91c6aa8347c8bac5342816163ea1 [{"artifact_path":"model","flavors":{"python_function":{"predict_fn":"predict","model_path":"model.pkl","loader_module":"mlflow.sklearn","env":{"conda":"conda.yaml","virtualenv":"python_env.yaml"},"python_version":"3.10.12"},"sklearn":{"pickled_model":"model.pkl","sklearn_version":"1.1.1","serialization_format":"cloudpickle","code":null}},"utc_time_created":"2024-12-20 19:41:11.678148"}] ad394c 087a91c6aa8347c8bac5342816163ea1 hyperoptAutoTracking DecisionTreeClassifier 7fa2d1272f494e66b1aceabeec04a643 368426492796581 FINISHED dbfs:/databricks/mlflow-tracking/368426492796581/7fa2d1272f494e66b1aceabeec04a643/artifacts 2024-12-20T19:41:01.447Z 2024-12-20T19:41:20.703Z 0.7212766528912271 0.7642836934347872 0.7662776355725102 0.7344581257949605 -0.7420419858169841 0.7638453116503049 0.7642836934347872 0.8472376217875621 0.7641048555257671 0.7642836934347872 0.7420419858169841 0.4762654969782097 16.0 best None entropy 22 11.0 None 22.0 1 1 0.0 None 0.0 16 11 0.0 None #7d54b2 labuser8100238_1734722509@vocareum.com success intrigued-turtle-718 sklearn.tree._classes.DecisionTreeClassifier 087a91c6aa8347c8bac5342816163ea1 [{"artifact_path":"model","flavors":{"python_function":{"predict_fn":"predict","model_path":"model.pkl","loader_module":"mlflow.sklearn","env":{"conda":"conda.yaml","virtualenv":"python_env.yaml"},"python_version":"3.10.12"},"sklearn":{"pickled_model":"model.pkl","sklearn_version":"1.1.1","serialization_format":"cloudpickle","code":null}},"utc_time_created":"2024-12-20 19:41:13.416098"}] ad394c 087a91c6aa8347c8bac5342816163ea1 hyperoptAutoTracking DecisionTreeClassifier aebb63d6bd0748688c186b61acdb8b37 368426492796581 FINISHED dbfs:/databricks/mlflow-tracking/368426492796581/aebb63d6bd0748688c186b61acdb8b37/artifacts 2024-12-20T19:41:02.44Z 2024-12-20T19:41:21.315Z 0.7162671788137907 0.7745432345101776 0.7761488534268884 0.7291273778861087 -0.7368568413767859 0.7742180971758394 0.7745432345101776 0.8614060591392798 0.7587429252308608 0.7745432345101776 0.7368568413767859 0.45299079415063226 4.0 best None entropy 39 13.0 None 39.0 1 1 0.0 None 0.0 4 13 0.0 None #e87b9f labuser8100238_1734722509@vocareum.com success nebulous-bass-620 sklearn.tree._classes.DecisionTreeClassifier 087a91c6aa8347c8bac5342816163ea1 [{"artifact_path":"model","flavors":{"python_function":{"predict_fn":"predict","model_path":"model.pkl","loader_module":"mlflow.sklearn","

### Find the Best Run - PySpark API

Alternatively, you can read experiment results into a PySpark DataFrame and use standard Spark expressions to search runs in an experiment.

In [0]:
import pyspark.sql.functions as sfn

all_experiment_runs_df = spark.read.format("mlflow-experiment")\
  .load(parent_run.info.experiment_id)

hpo_runs_df = all_experiment_runs_df.where(f"tags['mlflow.parentRunId'] = '{parent_run.info.run_id}' AND status = 'FINISHED'")\
  .withColumn("cv_f1", sfn.col("metrics").getItem('cv_f1'))\
  .orderBy(sfn.col("cv_f1").desc() )

display(hpo_runs_df)

run_id experiment_id metrics params tags start_time end_time status artifact_uri cv_f1 84a3c7a78eae445e9e385e54e45235fd 368426492796581 Map(training_precision_score -> 0.7638499686468617, cv_precision -> 0.7166073025685853, cv_accuracy -> 0.736364076484007, training_recall_score -> 0.7618863260717423, training_roc_auc -> 0.8422767781862777, training_score -> 0.7618863260717423, training_log_loss -> 0.484407069875055, cv_recall -> 0.7819779565087875, loss -> -0.7477902930835063, training_accuracy_score -> 0.7618863260717423, training_f1_score -> 0.7614462413451514, cv_f1 -> 0.7477902930835063) Map(splitter -> best, criterion -> gini, min_samples_leaf -> 12, dtree_criterion -> 0, max_depth -> 10, max_features -> None, random_state -> None, dtree_max_depth -> 1, class_weight -> None, dtree_min_samples_leaf -> 12.0, dtree_max_depth_int -> 10.0, ccp_alpha -> 0.0, min_samples_split -> 33, dtree_min_samples_split -> 33.0, max_leaf_nodes -> None, min_weight_fraction_leaf -> 0.0, min_impurity_decrease -> 0.0) Map(mlflow.log-model.history -> [{"artifact_path":"model","flavors":{"python_function":{"predict_fn":"predict","model_path":"model.pkl","loader_module":"mlflow.sklearn","env":{"conda":"conda.yaml","virtualenv":"python_env.yaml"},"python_version":"3.10.12"},"sklearn":{"pickled_model":"model.pkl","sklearn_version":"1.1.1","serialization_format":"cloudpickle","code":null}},"utc_time_created":"2024-12-20 19:41:11.678148"}], mlflow.parentRunId -> 087a91c6aa8347c8bac5342816163ea1, fmin_uuid -> ad394c, mlflow.runName -> crawling-elk-932, mlflow.rootRunId -> 087a91c6aa8347c8bac5342816163ea1, estimator_class -> sklearn.tree._classes.DecisionTreeClassifier, trial_status -> success, runSource -> hyperoptAutoTracking, mlflow.runColor -> #da4c4c, mlflow.user -> labuser8100238_1734722509@vocareum.com, estimator_name -> DecisionTreeClassifier) 2024-12-20T19:40:59.425Z 2024-12-20T19:41:19.116Z FINISHED dbfs:/databricks/mlflow-tracking/368426492796581/84a3c7a78eae445e9e385e54e45235fd/artifacts 0.7477902930835063 7fa2d1272f494e66b1aceabeec04a643 368426492796581 Map(training_precision_score -> 0.7662776355725102, cv_precision -> 0.7212766528912271, cv_accuracy -> 0.7344581257949605, training_recall_score -> 0.7642836934347872, training_roc_auc -> 0.8472376217875621, training_score -> 0.7642836934347872, training_log_loss -> 0.4762654969782097, cv_recall -> 0.7641048555257671, loss -> -0.7420419858169841, training_accuracy_score -> 0.7642836934347872, training_f1_score -> 0.7638453116503049, cv_f1 -> 0.7420419858169841) Map(splitter -> best, criterion -> entropy, min_samples_leaf -> 16, dtree_criterion -> 1, max_depth -> 11, max_features -> None, random_state -> None, dtree_max_depth -> 1, class_weight -> None, dtree_min_samples_leaf -> 16.0, dtree_max_depth_int -> 11.0, ccp_alpha -> 0.0, min_samples_split -> 22, dtree_min_samples_split -> 22.0, max_leaf_nodes -> None, min_weight_fraction_leaf -> 0.0, min_impurity_decrease -> 0.0) Map(mlflow.log-model.history -> [{"artifact_path":"model","flavors":{"python_function":{"predict_fn":"predict","model_path":"model.pkl","loader_module":"mlflow.sklearn","env":{"conda":"conda.yaml","virtualenv":"python_env.yaml"},"python_version":"3.10.12"},"sklearn":{"pickled_model":"model.pkl","sklearn_version":"1.1.1","serialization_format":"cloudpickle","code":null}},"utc_time_created":"2024-12-20 19:41:13.416098"}], mlflow.parentRunId -> 087a91c6aa8347c8bac5342816163ea1, fmin_uuid -> ad394c, mlflow.runName -> intrigued-turtle-718, mlflow.rootRunId -> 087a91c6aa8347c8bac5342816163ea1, estimator_class -> sklearn.tree._classes.DecisionTreeClassifier, trial_status -> success, runSource -> hyperoptAutoTracking, mlflow.runColor -> #7d54b2, mlflow.user -> labuser8100238_1734722509@vocareum.com, estimator_name -> DecisionTreeClassifier) 2024-12-20T19:41:01.447Z 2024-12-20T19:41:20.703Z FINISHED dbfs:/databricks/mlflow-tracking/368426492796581/7fa2d1272f494e66b1aceabeec04a643/artifacts 0.7420419858169841 aebb63d6bd0748688c186b61

### Find the Best Run - MLflow UI

The simplest way of seeing the tuning result is to use MLflow UI. 

* Click on **Experiments** from left menu.

* Select experiment which has the same name as this notebook's title (**2.1 - Hyperparameter Tuning with Hyperopt**).

* View the **parent run** and **nested child runs**. 

* You can filter and order by metrics and other model metadata.


## Clean up Classroom

Run the following cell to remove lessons-specific assets created during this lesson.

In [0]:
DA.cleanup()

Resetting the learning environment:
| dropping the catalog "labuser8100238_1734722509_1v9p_da"...(0 seconds)

Validating the locally installed datasets:
| listing local files...(0 seconds)
| validation completed...(0 seconds total)



## Conclusion

To sum it up, this demo has shown you the process of tuning your models using Hyperopt and MLflow. You've learned a method to fine-tune your model settings through Bayesian optimization and how to keep tabs on the whole tuning journey with MLflow. Moving forward, these tools will be instrumental in improving your model's performance and simplifying the process of fine-tuning machine learning models.


&copy; 2024 Databricks, Inc. All rights reserved.<br/>
Apache, Apache Spark, Spark and the Spark logo are trademarks of the 
<a href="https://www.apache.org/">Apache Software Foundation</a>.<br/>
<br/><a href="https://databricks.com/privacy-policy">Privacy Policy</a> | 
<a href="https://databricks.com/terms-of-use">Terms of Use</a> | 
<a href="https://help.databricks.com/">Support</a>